<a href="https://colab.research.google.com/github/SasikaA073/MSLTNet/blob/main/Video_Exposure_Correction_MSLT_colab.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
!git clone https://github.com/SasikaA073/MSLTNet.git

Cloning into 'MSLTNet'...
remote: Enumerating objects: 555, done.
remote: Counting objects: 100% (75/75), done.
remote: Compressing objects: 100% (58/58), done.
remote: Total 555 (delta 30), reused 44 (delta 16), pack-reused 480 (from 1)
Receiving objects: 100% (555/555), 61.99 MiB | 17.29 MiB/s, done.
Resolving deltas: 100% (125/125), done.


In [2]:
import sys
sys.path.insert(0,"/content/MSLTNet")

In [25]:
import cv2
import os
import torch
import torchvision
from torchvision import transforms
from pyramid_structure.Omi_LP import MSLT
from torch.utils.data import DataLoader
import dataset.loaddata as loaddata
from merge_videos import merge_videos_side_by_side
import time

def process_video(video_name, video_path, output_folder, model_path):
    print("Starting video processing...")

    # Create output folders
    frames_folder = os.path.join(output_folder, "frames")
    results_folder = os.path.join(output_folder, "results")
    os.makedirs(frames_folder, exist_ok=True)
    os.makedirs(results_folder, exist_ok=True)
    print("Output folders created.")

    # Load the video
    cap = cv2.VideoCapture(video_path)
    fps = cap.get(cv2.CAP_PROP_FPS)
    frame_count = int(cap.get(cv2.CAP_PROP_FRAME_COUNT))
    print(f"Video loaded. FPS: {fps}, Total frames: {frame_count}")

    # Split the video into frames
    print("Splitting video into frames...")
    frame_paths = []
    for i in range(frame_count):
        ret, frame = cap.read()
        if not ret:
            break
        frame_path = os.path.join(frames_folder, f"frame_{i:04d}.jpg")
        cv2.imwrite(frame_path, frame)
        frame_paths.append(frame_path)
        if (i + 1) % 100 == 0:
            print(f"Processed {i + 1}/{frame_count} frames")

    print(f"TODO: frame_paths >>")
    print(frame_paths)

    cap.release()
    print("Video split into frames completed.")

    # Load and prepare the model
    print("Loading and preparing the model...")
    device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
    model = MSLT().to(device)
    model.load_state_dict(torch.load(model_path, map_location=device))
    model.eval()
    print(f"Model loaded and prepared. Using device: {device}")

    # Prepare data transforms
    transform = transforms.Compose([
        transforms.ToTensor(),
    ])

    # Process the frames using the model
    print("Processing frames using the model...")
    with torch.no_grad():
        for i, frame_path in enumerate(frame_paths):
            # Load and preprocess the frame
            frame = cv2.imread(frame_path)
            frame = cv2.cvtColor(frame, cv2.COLOR_BGR2RGB)
            frame_tensor = transform(frame).unsqueeze(0).to(device)

            # Process the frame
            output = model(frame_tensor)

            # Save the result
            result_path = os.path.join(results_folder, f"result_{i:04d}.jpg")
            torchvision.utils.save_image(output, result_path)

            if (i + 1) % 100 == 0:
                print(f"Processed {i + 1}/{len(frame_paths)} frames")

    print("Frame processing completed.")

    # Convert the frames back to video
    print("Converting processed frames back to video...")
    [video_name,video_ftype] = video_name.split(".")

    output_video_path = os.path.join(output_folder, f"output_{video_name}.{video_ftype}")
    frame = cv2.imread(os.path.join(results_folder, "result_0000.jpg"))

    height, width, layers = frame.shape
    fourcc = cv2.VideoWriter_fourcc(*'mp4v')
    out = cv2.VideoWriter(output_video_path, fourcc, fps, (width, height))

    for i in range(frame_count):
        result_path = os.path.join(results_folder, f"result_{i:04d}.jpg")
        frame = cv2.imread(result_path)
        out.write(frame)
        if (i + 1) % 100 == 0:
            print(f"Added {i + 1}/{frame_count} frames to video")

    out.release()
    print("Video conversion completed.")

    print(f"Video processing complete. Output saved to {output_video_path}")

## Download the video into sample_video folder

In [ ]:
!wget

In [21]:
video_files = [file for file in os.listdir("/content/MSLTNet/sample_video") if file.endswith((".mp4", ".avi", ".mov", ".flv", ".mpeg", ".mpg", ".wmv", ".webm", ".mkv"
                                                                                , ".MP4", ".AVI", ".MOV", ".FLV", ".MPEG", ".MPG", ".WMV", ".WEBM", ".MKV"))]

print("Available video files:")
for i, file in enumerate(video_files):
    print(f"{i + 1}. {file}")

video_index = int(input("Enter the index of the video file you want to process: "))
video_name = video_files[video_index - 1]

video_path = os.path.join("sample_video", video_name)
# video_name = "5 Second Countdown HD.mp4"
# video_path = "/content/5 Second Countdown HD.mp4"
print(video_path)

Available video files:
1. video_1_1080p.mp4
2. video_1_720p.mp4
Enter the index of the video file you want to process: 2
/content/MSLTNet/sample_video/video_1_720p.mp4


In [23]:
output_folder = os.path.join("/content/MSLTNet/sample_video/output_folder", f"output_{video_name}")
os.makedirs(output_folder, exist_ok=True)

model_path = "/content/MSLTNet/pretrained_model/mslt+.pth"

In [26]:
print(f"\nProcessing video: {video_name}")
start_time = time.time()
process_video(video_name, video_path, output_folder, model_path)
# print the time taken in seconds upto 2 decimal places
print("Time taken: {:.2f} seconds".format(time.time() - start_time))


Processing video: video_1_720p.mp4
Starting video processing...
Output folders created.
Video loaded. FPS: 25.0, Total frames: 650
Splitting video into frames...
Processed 100/650 frames
Processed 200/650 frames
Processed 300/650 frames
Processed 400/650 frames
Processed 500/650 frames
Processed 600/650 frames


  model.load_state_dict(torch.load(model_path, map_location=device))



TODO: frame_paths >>
['/content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/frames/frame_0000.jpg', '/content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/frames/frame_0001.jpg', '/content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/frames/frame_0002.jpg', '/content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/frames/frame_0003.jpg', '/content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/frames/frame_0004.jpg', '/content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/frames/frame_0005.jpg', '/content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/frames/frame_0006.jpg', '/content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/frames/frame_0007.jpg', '/content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/frames/frame_0008.jpg', '/content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/frames/frame_0009.jpg', '/content/MSLTNet/sample_video/output_folder/out

  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]



Processed 100/650 frames
Processed 200/650 frames
Processed 300/650 frames
Processed 400/650 frames
Processed 500/650 frames
Processed 600/650 frames
Frame processing completed.
Converting processed frames back to video...
Added 100/650 frames to video
Added 200/650 frames to video
Added 300/650 frames to video
Added 400/650 frames to video
Added 500/650 frames to video
Added 600/650 frames to video
Video conversion completed.
Video processing complete. Output saved to /content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/output_video_1_720p.mp4
Time taken: 49.17 seconds


In [28]:
# Delete frames and results folders
frames_folder = os.path.join(output_folder, "frames")
results_folder = os.path.join(output_folder, "results")
os.system(f"rm -r {frames_folder}")
os.system(f"rm -r {results_folder}")

256

In [31]:
input_video_path = video_path
output_video_path = os.path.join(output_folder, f"output_{video_name}.{video_ftype}")
merged_video_dir = "sample_video/merged_folder"
os.makedirs(merged_video_dir, exist_ok=True)  # Create the directory if it doesn't exist
merged_video_path = os.path.join(merged_video_dir, f"merged_{video_name}.{video_ftype}")

# Verify that input files exist
if not os.path.exists(input_video_path):
    raise FileNotFoundError(f"Input video not found: {input_video_path}")
if not os.path.exists(output_video_path):
    raise FileNotFoundError(f"Output video not found: {output_video_path}")

print(f"Input video path: {input_video_path}")
print(f"Output video path: {output_video_path}")
print(f"Merged video will be saved to: {merged_video_path}")

merge_videos_side_by_side(input_video_path, output_video_path, merged_video_path)

Input video path: /content/MSLTNet/sample_video/video_1_720p.mp4
Output video path: /content/MSLTNet/sample_video/output_folder/output_video_1_720p.mp4/output_video_1_720p.mp4
Merged video will be saved to: sample_video/merged_folder/merged_video_1_720p.mp4


t:   0%|          | 2/650 [03:15<17:37:35, 97.93s/it, now=None]

Moviepy - Building video sample_video/merged_folder/merged_video_1_720p.mp4.
MoviePy - Writing audio in merged_video_1_720pTEMP_MPY_wvf_snd.mp4



t:   0%|          | 2/650 [03:16<17:41:08, 98.25s/it, now=None]

MoviePy - Done.
Moviepy - Writing video sample_video/merged_folder/merged_video_1_720p.mp4




t:   0%|          | 2/650 [04:15<23:01:40, 127.93s/it, now=None]

Moviepy - Done !
Moviepy - video ready sample_video/merged_folder/merged_video_1_720p.mp4


In [32]:
from IPython.display import Video

# Path to the video file (change this if your path is different)
video_path = '/content/MSLTNet/sample_video/merged_folder/merged_video_1_720p.mp4'

# Display the video
Video(video_path, embed=True, width=720, height=400)
